In [1]:
import gym
import numpy as np
rm='Pong-v0'

In [2]:
%matplotlib inline
from matplotlib import animation
import matplotlib.pyplot as plt
from IPython.display import display, HTML

def display_frames_as_gif(frames):
    plt.figure(figsize=(frames[0].shape[1] / 72.0, frames[0].shape[0] / 72.0), dpi = 144)
    patch = plt.imshow(frames[0])
    plt.axis('off')
    def animate(i):
        patch.set_data(frames[i])
    anim = animation.FuncAnimation(plt.gcf(), animate, frames = len(frames), interval=50)
    plt.close(anim._fig)
    display(HTML(anim.to_jshtml()))

from gym.wrappers import AtariPreprocessing
gym.new_step_api=True
env = gym.make(rm)

H = 200 # number of hidden layer neurons
D = 80 * 80 # input dimensionality: 80x80 grid
model = {}
model['W1'] = np.random.randn(H,D) / np.sqrt(D) # "Xavier" initialization
model['W2'] = np.random.randn(H) / np.sqrt(H)
# hyperparameters
batch_size = 10 # every how many episodes to do a param update?
learning_rate = 1e-2
gamma = 0.99 # discount factor for reward
decay_rate = 0.99 # decay factor for RMSProp leaky sum of grad^2
grad_buffer = { k : np.zeros_like(v) for k,v in model.items() } # update buffers that add up gradients over a batch
rmsprop_cache = { k : np.zeros_like(v) for k,v in model.items() } # rmsprop memory

def sigmoid(x): 
  return 1.0 / (1.0 + np.exp(-x)) # sigmoid "squashing" function to interval [0,1]

def prepro(I):
  I=np.asarray(I)
  I = I[35:195] # crop
  I = I[::2,::2,0] # downsample by factor of 2
  
  I[I == 144] = 0 # erase background (background type 1)
  
  I[I == 109] = 0 # erase background (background type 2)
  
  I[I != 0] = 1 # everything else (paddles, ball) just set to 1
  return I.astype(float).ravel()

def discount_rewards(r):
  discounted_r = np.zeros_like(r)
  running_add = 0
  for t in reversed(range(0, r.size)):
    if r[t] != 0: running_add = 0 # reset the sum, since this was a game boundary (pong specific!)
    running_add = running_add * gamma + r[t]
    discounted_r[t] = running_add
  return discounted_r

def policy_forward(x):
  h = np.dot(model['W1'], x)
  h[h<0] = 0 # ReLU nonlinearity
  logp = np.dot(model['W2'], h)
  p = sigmoid(logp)
  return p, h # return probability of taking action 2, and hidden state

def policy_backward(epx, eph, epdlogp):
  """ backward pass. (eph is array of intermediate hidden states) """
  dW2 = np.dot(eph.T, epdlogp).ravel()
  dh = np.outer(epdlogp, model['W2'])
  dh[eph <= 0] = 0 # backpro prelu
  dW1 = np.dot(dh.T, epx)
  return {'W1':dW1, 'W2':dW2}

def model_step(model, observation, prev_x):

  cur_x = prepro(observation)
  x = cur_x - prev_x if prev_x is not None else np.zeros(D)
  prev_x = cur_x
  
  # forward the policy network and sample an action from the returned probability
  aprob, _ = policy_forward(x)
  action = 2 if aprob >= 0.5 else 3 # roll the dice!
  
  return action, prev_x

def play_game(env, model):
  observation = env.reset()

  frames = []
  cumulated_reward = 0

  prev_x = None # used in computing the difference frame

  for t in range(1000):
      frames.append(env.render(mode = 'rgb_array'))
      action, prev_x = model_step(model, observation, prev_x)
      observation, reward, done, info = env.step(action)
      cumulated_reward += reward
      if done:
          print("Episode finished after {} timesteps, accumulated reward = {}".format(t+1, cumulated_reward))
          break
  print("Episode finished without success, accumulated reward = {}".format(cumulated_reward))
  env.close()
  display_frames_as_gif(frames)

def train_model(env, model, total_episodes = 100):
  hist = []
  observation = env.reset()

  prev_x = None # used in computing the difference frame
  xs,hs,dlogps,drs = [],[],[],[]
  running_reward = None
  reward_sum = 0
  episode_number = 0

  while True:
  
    cur_x = prepro(observation)
    x = cur_x - prev_x if prev_x is not None else np.zeros(D)
    prev_x = cur_x

    # forward the policy network and sample an action from the returned probability
    aprob, h = policy_forward(x)
    action = 2 if np.random.uniform() < aprob else 3 # roll the dice!

    # record various intermediates (needed later for backprop)
    xs.append(x) # observation
    hs.append(h) # hidden state
    y = 1 if action == 2 else 0 # a "fake label"
    dlogps.append(y - aprob) # grad that encourages the action that was taken to be taken (see http://cs231n.github.io/neural-networks-2/#losses if confused)

    # step the environment and get new measurements
    observation, reward, done, info = env.step(action)
    reward_sum += reward

    drs.append(reward) # record reward (has to be done after we call step() to get reward for previous action)

    if done: # an episode finished
      episode_number += 1

      # stack together all inputs, hidden states, action gradients, and rewards for this episode
      epx = np.vstack(xs)
      eph = np.vstack(hs)
      epdlogp = np.vstack(dlogps)
      epr = np.vstack(drs)
      xs,hs,dlogps,drs = [],[],[],[] # reset array memory

      # compute the discounted reward backwards through time
      discounted_epr = discount_rewards(epr)
      # standardize the rewards to be unit normal (helps control the gradient estimator variance)
      discounted_epr -= np.mean(discounted_epr)
      discounted_epr /= np.std(discounted_epr)

      epdlogp *= discounted_epr # modulate the gradient with advantage (PG magic happens right here.)
      grad = policy_backward(epx, eph, epdlogp)
      for k in model: grad_buffer[k] += grad[k] # accumulate grad over batch

      # perform rmsprop parameter update every batch_size episodes
      if episode_number % batch_size == 0:
        for k,v in model.items():
          g = grad_buffer[k] # gradient
          rmsprop_cache[k] = decay_rate * rmsprop_cache[k] + (1 - decay_rate) * g**2
          model[k] += learning_rate * g / (np.sqrt(rmsprop_cache[k]) + 1e-5)
          grad_buffer[k] = np.zeros_like(v) # reset batch gradient buffer

      # boring book-keeping
      running_reward = reward_sum if running_reward is None else running_reward * 0.99 + reward_sum * 0.01
      hist.append((episode_number, reward_sum, running_reward))
      print ('episode %f, reward total was %f. running mean: %f' % (episode_number, reward_sum, running_reward))
      reward_sum = 0
      observation = env.reset() # reset env
      prev_x = None
      if episode_number == total_episodes: 
        return hist

    # if reward != 0: # Pong has either +1 or -1 reward exactly when game ends.
    #   print('ep {}: game finished, reward: {}'.format(episode_number, reward) + ('' if reward == -1 else ' !!!!!!!!'))

C:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\gym\envs\registration.py:592: UserWarning: WARN: The environment Pong-v0 is out of date. You should consider upgrading to version `v4`.
  logger.warn(
C:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\gym\core.py:329: DeprecationWarning: WARN: Initializing wrapper in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  deprecation(
C:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\gym\wrappers\step_api_compatibility.py:39: DeprecationWarning: WARN: Initializing environment in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  deprecation(


In [3]:
%time hist1 = train_model(env, model, total_episodes=6000)

C:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\gym\utils\passive_env_checker.py:227: DeprecationWarning: WARN: Core environment is written in old step API which returns one bool instead of two. It is recommended to rewrite the environment with new step API. 
  logger.deprecation(


episode 1.000000, reward total was -21.000000. running mean: -21.000000
episode 2.000000, reward total was -21.000000. running mean: -21.000000
episode 3.000000, reward total was -19.000000. running mean: -20.980000
episode 4.000000, reward total was -19.000000. running mean: -20.960200
episode 5.000000, reward total was -21.000000. running mean: -20.960598
episode 6.000000, reward total was -21.000000. running mean: -20.960992
episode 7.000000, reward total was -20.000000. running mean: -20.951382
episode 8.000000, reward total was -19.000000. running mean: -20.931868
episode 9.000000, reward total was -20.000000. running mean: -20.922550
episode 10.000000, reward total was -21.000000. running mean: -20.923324
episode 11.000000, reward total was -21.000000. running mean: -20.924091
episode 12.000000, reward total was -21.000000. running mean: -20.924850
episode 13.000000, reward total was -21.000000. running mean: -20.925601
episode 14.000000, reward total was -21.000000. running mean

episode 114.000000, reward total was -21.000000. running mean: -20.819865
episode 115.000000, reward total was -21.000000. running mean: -20.821666
episode 116.000000, reward total was -21.000000. running mean: -20.823450
episode 117.000000, reward total was -21.000000. running mean: -20.825215
episode 118.000000, reward total was -21.000000. running mean: -20.826963
episode 119.000000, reward total was -21.000000. running mean: -20.828693
episode 120.000000, reward total was -21.000000. running mean: -20.830406
episode 121.000000, reward total was -20.000000. running mean: -20.822102
episode 122.000000, reward total was -21.000000. running mean: -20.823881
episode 123.000000, reward total was -21.000000. running mean: -20.825642
episode 124.000000, reward total was -20.000000. running mean: -20.817386
episode 125.000000, reward total was -21.000000. running mean: -20.819212
episode 126.000000, reward total was -20.000000. running mean: -20.811020
episode 127.000000, reward total was -

episode 225.000000, reward total was -20.000000. running mean: -20.552760
episode 226.000000, reward total was -20.000000. running mean: -20.547232
episode 227.000000, reward total was -20.000000. running mean: -20.541760
episode 228.000000, reward total was -21.000000. running mean: -20.546342
episode 229.000000, reward total was -21.000000. running mean: -20.550879
episode 230.000000, reward total was -21.000000. running mean: -20.555370
episode 231.000000, reward total was -20.000000. running mean: -20.549817
episode 232.000000, reward total was -19.000000. running mean: -20.534318
episode 233.000000, reward total was -20.000000. running mean: -20.528975
episode 234.000000, reward total was -21.000000. running mean: -20.533685
episode 235.000000, reward total was -18.000000. running mean: -20.508349
episode 236.000000, reward total was -20.000000. running mean: -20.503265
episode 237.000000, reward total was -21.000000. running mean: -20.508232
episode 238.000000, reward total was -

episode 336.000000, reward total was -18.000000. running mean: -20.092621
episode 337.000000, reward total was -21.000000. running mean: -20.101695
episode 338.000000, reward total was -20.000000. running mean: -20.100678
episode 339.000000, reward total was -21.000000. running mean: -20.109671
episode 340.000000, reward total was -21.000000. running mean: -20.118574
episode 341.000000, reward total was -21.000000. running mean: -20.127389
episode 342.000000, reward total was -19.000000. running mean: -20.116115
episode 343.000000, reward total was -19.000000. running mean: -20.104954
episode 344.000000, reward total was -18.000000. running mean: -20.083904
episode 345.000000, reward total was -18.000000. running mean: -20.063065
episode 346.000000, reward total was -21.000000. running mean: -20.072434
episode 347.000000, reward total was -20.000000. running mean: -20.071710
episode 348.000000, reward total was -19.000000. running mean: -20.060993
episode 349.000000, reward total was -

...

episode 5515.000000, reward total was -6.000000. running mean: -9.354381
episode 5516.000000, reward total was -11.000000. running mean: -9.370837
episode 5517.000000, reward total was -14.000000. running mean: -9.417128
episode 5518.000000, reward total was -2.000000. running mean: -9.342957
episode 5519.000000, reward total was -14.000000. running mean: -9.389528
episode 5520.000000, reward total was -11.000000. running mean: -9.405632
episode 5521.000000, reward total was -8.000000. running mean: -9.391576
episode 5522.000000, reward total was -5.000000. running mean: -9.347660
episode 5523.000000, reward total was -15.000000. running mean: -9.404184
episode 5524.000000, reward total was -12.000000. running mean: -9.430142
episode 5525.000000, reward total was -12.000000. running mean: -9.455840
episode 5526.000000, reward total was -6.000000. running mean: -9.421282
episode 5527.000000, reward total was -15.000000. running mean: -9.477069
episode 5528.000000, reward total was -15.0

episode 5627.000000, reward total was -17.000000. running mean: -9.125619
episode 5628.000000, reward total was -8.000000. running mean: -9.114363
episode 5629.000000, reward total was -10.000000. running mean: -9.123219
episode 5630.000000, reward total was -17.000000. running mean: -9.201987
episode 5631.000000, reward total was -6.000000. running mean: -9.169967
episode 5632.000000, reward total was -15.000000. running mean: -9.228268
episode 5633.000000, reward total was -13.000000. running mean: -9.265985
episode 5634.000000, reward total was -15.000000. running mean: -9.323325
episode 5635.000000, reward total was -17.000000. running mean: -9.400092
episode 5636.000000, reward total was -15.000000. running mean: -9.456091
episode 5637.000000, reward total was -11.000000. running mean: -9.471530
episode 5638.000000, reward total was -15.000000. running mean: -9.526815
episode 5639.000000, reward total was -9.000000. running mean: -9.521547
episode 5640.000000, reward total was -9.

episode 5739.000000, reward total was -5.000000. running mean: -9.428242
episode 5740.000000, reward total was -11.000000. running mean: -9.443960
episode 5741.000000, reward total was -15.000000. running mean: -9.499520
episode 5742.000000, reward total was -7.000000. running mean: -9.474525
episode 5743.000000, reward total was -3.000000. running mean: -9.409780
episode 5744.000000, reward total was -12.000000. running mean: -9.435682
episode 5745.000000, reward total was -4.000000. running mean: -9.381325
episode 5746.000000, reward total was -13.000000. running mean: -9.417512
episode 5747.000000, reward total was -5.000000. running mean: -9.373337
episode 5748.000000, reward total was -7.000000. running mean: -9.349604
episode 5749.000000, reward total was -5.000000. running mean: -9.306108
episode 5750.000000, reward total was -18.000000. running mean: -9.393046
episode 5751.000000, reward total was -8.000000. running mean: -9.379116
episode 5752.000000, reward total was -5.00000

episode 5850.000000, reward total was -1.000000. running mean: -9.980791
episode 5851.000000, reward total was -19.000000. running mean: -10.070983
episode 5852.000000, reward total was -14.000000. running mean: -10.110273
episode 5853.000000, reward total was -12.000000. running mean: -10.129170
episode 5854.000000, reward total was -15.000000. running mean: -10.177879
episode 5855.000000, reward total was -4.000000. running mean: -10.116100
episode 5856.000000, reward total was -12.000000. running mean: -10.134939
episode 5857.000000, reward total was -13.000000. running mean: -10.163589
episode 5858.000000, reward total was -11.000000. running mean: -10.171954
episode 5859.000000, reward total was -15.000000. running mean: -10.220234
episode 5860.000000, reward total was 1.000000. running mean: -10.108032
episode 5861.000000, reward total was -12.000000. running mean: -10.126951
episode 5862.000000, reward total was -10.000000. running mean: -10.125682
episode 5863.000000, reward to

episode 5961.000000, reward total was -12.000000. running mean: -9.966117
episode 5962.000000, reward total was -5.000000. running mean: -9.916456
episode 5963.000000, reward total was -5.000000. running mean: -9.867292
episode 5964.000000, reward total was -4.000000. running mean: -9.808619
episode 5965.000000, reward total was -16.000000. running mean: -9.870533
episode 5966.000000, reward total was -8.000000. running mean: -9.851827
episode 5967.000000, reward total was 4.000000. running mean: -9.713309
episode 5968.000000, reward total was -8.000000. running mean: -9.696176
episode 5969.000000, reward total was -5.000000. running mean: -9.649214
episode 5970.000000, reward total was -11.000000. running mean: -9.662722
episode 5971.000000, reward total was -1.000000. running mean: -9.576095
episode 5972.000000, reward total was -13.000000. running mean: -9.610334
episode 5973.000000, reward total was -7.000000. running mean: -9.584230
episode 5974.000000, reward total was -9.000000.

In [4]:
play_game(env, model)

C:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\gym\core.py:51: DeprecationWarning: WARN: The argument mode in render method is deprecated; use render_mode during environment initialization instead.
See here for more information: https://www.gymlibrary.ml/content/api/
  deprecation(
C:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\gym\utils\passive_env_checker.py:297: UserWarning: WARN: No render fps was declared in the environment (env.metadata['render_fps'] is None or not defined), rendering may occur at inconsistent fps.
  logger.warn(


Episode finished without success, accumulated reward = -3.0
